In [14]:
import pandas as pd

# Load the CSV files into DataFrames
stations_df = pd.read_csv(r'C:\Users\npwol\Downloads\ca_counties\ContinuousMonitoringStation_20240815171202.csv')
cities_df = pd.read_csv(r'C:\Users\npwol\Downloads\ca_counties\California_cities.csv')


In [15]:
# Define blank columns to add to the stations_df
blank_columns = ['city', 'population_total', 'area_total_sq_mi']

# Add blank columns
for column in blank_columns:
    stations_df[column] = pd.NA


In [16]:
# Rename columns in cities_df to match the columns in stations_df
cities_df = cities_df.rename(columns={
    'latd': 'latitude',
    'longd': 'longitude'
})

# Merge the DataFrames on latitude and longitude
merged_df = pd.merge(stations_df, cities_df[['city', 'population_total', 'area_total_sq_mi', 'latitude', 'longitude']],
                     on=['latitude', 'longitude'],
                     how='left')


In [17]:
from sqlalchemy import create_engine

# Create an in-memory SQLite database
engine = create_engine('sqlite:///:memory:')


In [18]:
# Write DataFrames to SQL tables
stations_df.to_sql('stations', con=engine, index=False)
cities_df.to_sql('cities', con=engine, index=False)


482

In [19]:
# Define the SQL query to merge DataFrames
query = """
SELECT s.*, c.city, c.population_total, c.area_total_sq_mi
FROM stations s
LEFT JOIN cities c
ON s.latitude = c.latitude AND s.longitude = c.longitude
"""

# Execute the query and fetch the result into a DataFrame
merged_df_sql = pd.read_sql_query(query, con=engine)


In [20]:
print(merged_df_sql.head())


  station_number                                       station_name  \
0         A85710                           Alder Creek at Glenbrook   
1  12N04E03N003M  Am. Basin Well 1  mid-shall scrn 390-400,510-5...   
2  12N04E03N001M   American Basin Well 1 deep screen 950-970 ft bgs   
3  12N04E03N002M  American Basin Well 1 middle-deep screen 680-7...   
4  12N04E03N004M  American Basin Well 1 shallow screen 170-180 f...   

     station_short_name   station_type cdec_id           site_code   latitude  \
0  Alder Cr @ Glenbrook  Surface Water    None                None  38.851583   
1   AB-1 Middle-Shallow    Groundwater    None  389117N1215238W001  38.911600   
2             AB-1 Deep    Groundwater    None  389116N1215238W001  38.911600   
3      AB-1 Middle-Deep    Groundwater    None  389116N1215238W002  38.911600   
4          AB-1 Shallow    Groundwater    None  389116N1215238W003  38.911600   

    longitude lldatum positional_accuracy  County  city population_total  \
0 -122.757

In [21]:
import pandas as pd
from bokeh.plotting import figure, show
from bokeh.io import output_notebook
from bokeh.models import ColumnDataSource, HoverTool

# Output to notebook
output_notebook()

# Load the CSV files into DataFrames
stations_df = pd.read_csv(r'C:\Users\npwol\Downloads\ca_counties\ContinuousMonitoringStation_20240815171202.csv')
cities_df = pd.read_csv(r'C:\Users\npwol\Downloads\ca_counties\California_cities.csv')

# Rename columns in cities_df to match the columns in stations_df
cities_df = cities_df.rename(columns={
    'latd': 'latitude',
    'longd': 'longitude'
})

# Merge the DataFrames on latitude and longitude
merged_df = pd.merge(stations_df, cities_df[['city', 'population_total', 'area_total_sq_mi', 'latitude', 'longitude']],
                     on=['latitude', 'longitude'],
                     how='left')


Loading BokehJS ...

In [22]:
# Sort cities by population and get the top 10 cities
top_10_cities = cities_df.sort_values(by='population_total', ascending=False).head(10)

# Define a function to scale marker sizes based on population
def scale_marker_size(population, min_size=20, max_size=40):
    min_pop, max_pop = top_10_cities['population_total'].min(), top_10_cities['population_total'].max()
    return min_size + (max_size - min_size) * (population - min_pop) / (max_pop - min_pop)

# Apply the function to get sizes for the top 10 cities
top_10_cities['size'] = top_10_cities['population_total'].apply(scale_marker_size)

# Create ColumnDataSources
stations_source = ColumnDataSource(merged_df)


In [23]:
from sklearn.cluster import KMeans
import pandas as pd

# Prepare data for K-means on cleaned data
# Ensure the columns 'latitude' and 'longitude' are correctly accessed as a DataFrame
coordinates_cleaned = merged_df[['latitude', 'longitude']].values

# Compute K-means with 4 clusters
kmeans = KMeans(n_clusters=4, random_state=0).fit(coordinates_cleaned)
merged_df['cluster'] = kmeans.labels_.astype(str)  # Assign cluster labels

# Optionally, you can add the cluster centers to the DataFrame or create a separate DataFrame
centroids_df = pd.DataFrame(kmeans.cluster_centers_, columns=['longitude', 'latitude'])
centroids_df['station_type'] = ['Centroid ' + str(i) for i in range(len(centroids_df))]

# Display the updated DataFrame and centroids
print(merged_df.head())
print(centroids_df)




  station_number                                       station_name  \
0         A85710                           Alder Creek at Glenbrook   
1  12N04E03N003M  Am. Basin Well 1  mid-shall scrn 390-400,510-5...   
2  12N04E03N001M   American Basin Well 1 deep screen 950-970 ft bgs   
3  12N04E03N002M  American Basin Well 1 middle-deep screen 680-7...   
4  12N04E03N004M  American Basin Well 1 shallow screen 170-180 f...   

     station_short_name   station_type cdec_id           site_code   latitude  \
0  Alder Cr @ Glenbrook  Surface Water     NaN                 NaN  38.851583   
1   AB-1 Middle-Shallow    Groundwater     NaN  389117N1215238W001  38.911600   
2             AB-1 Deep    Groundwater     NaN  389116N1215238W001  38.911600   
3      AB-1 Middle-Deep    Groundwater     NaN  389116N1215238W002  38.911600   
4          AB-1 Shallow    Groundwater     NaN  389116N1215238W003  38.911600   

    longitude lldatum positional_accuracy  County city  population_total  \
0 -122.757

c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(


In [26]:
import pandas as pd
from bokeh.plotting import figure, show
from bokeh.io import output_notebook
from bokeh.models import ColumnDataSource, HoverTool
from sklearn.cluster import KMeans

# Output to notebook (or use output_file() if running outside of Jupyter)
output_notebook()

# Load the CSV files into DataFrames
stations_df = pd.read_csv(r'C:\Users\npwol\Downloads\ca_counties\ContinuousMonitoringStation_20240815171202.csv')
cities_df = pd.read_csv(r'C:\Users\npwol\Downloads\ca_counties\California_cities.csv')

# Rename columns in cities_df to match the columns in stations_df
cities_df = cities_df.rename(columns={
    'latd': 'latitude',
    'longd': 'longitude'
})

# Merge the DataFrames on latitude and longitude
merged_df = pd.merge(stations_df, cities_df[['city', 'population_total', 'area_total_sq_mi', 'latitude', 'longitude']],
                     on=['latitude', 'longitude'],
                     how='left')

# Filter out 'Not known' and 'Unknown' station types
n_clusters_dict = {
    'Tide Station': 1,
    'Surface Water': 7,
    'Groundwater': 4,
    'Water Quality': 4
}

filtered_merged_df = merged_df[merged_df['station_type'].isin(n_clusters_dict.keys())]

# Initialize lists to hold the centroid data
centroids = []
cluster_labels = []

# Perform K-means clustering for each station_type bin
for station_type, n_clusters in n_clusters_dict.items():
    # Filter data for the current station_type
    type_merged_df = filtered_merged_df[filtered_merged_df['station_type'] == station_type].copy()
    
    # Prepare data for K-means clustering
    coordinates = type_merged_df[['longitude', 'latitude']].values
    
    # Perform K-means clustering with the specified number of clusters
    kmeans = KMeans(n_clusters=n_clusters, random_state=0).fit(coordinates)
    
    # Add cluster labels to the DataFrame
    type_merged_df['cluster'] = kmeans.labels_.astype(str)
    
    # Extract centroids and add to the list
    centroids.append(pd.DataFrame(kmeans.cluster_centers_, columns=['longitude', 'latitude'])
                     .assign(station_type=station_type, cluster=[str(i) for i in range(n_clusters)]))
    
    # Append the data with clusters to the list
    cluster_labels.append(type_merged_df)

# Combine all clustered data and centroids
combined_merged_df = pd.concat(cluster_labels, ignore_index=True)
centroids_merged_df = pd.concat(centroids, ignore_index=True)

# Define colors and markers for station types
station_type_colors = {
    'Surface Water': 'blue',        # Blue for Surface Water
    'Groundwater': 'darkgreen',     # Dark green for Groundwater
    'Water Quality': 'red',         # Red for Water Quality
    'Not known': 'grey',            # Grey for Not Known
    'Unknown': 'grey',              # Grey for Unknown
    'Tide Station': 'lightyellow'   # Yellow for Tide Station
}

station_type_markers = {
    'Surface Water': 'circle',    # Blue circle
    'Groundwater': 'square',      # Dark green square
    'Water Quality': 'triangle',  # Red triangle
    'Not known': '+',             # Grey plus sign
    'Unknown': '+',               # Grey plus sign
    'Tide Station': 'square'      # Yellow square
}

# Create a Bokeh plot with a very dark blue background
p = figure(width=1000, height=800, title="K-means Clustering by Station Type",
           x_axis_label='Longitude', y_axis_label='Latitude',
           x_range=(-125, -115), y_range=(30, 45),
           background_fill_color='#001f3f',  # Very dark blue background
           border_fill_color='#001f3f',
           outline_line_color='white')

# Plot all data points with their assigned colors and markers
for station_type, marker in station_type_markers.items():
    if station_type in combined_merged_df['station_type'].unique():
        type_df = combined_merged_df[combined_merged_df['station_type'] == station_type]
        p.scatter('longitude', 'latitude', source=ColumnDataSource(type_df),
                  color=station_type_colors.get(station_type, 'rgba(128,128,128,0.3)'),
                  marker=station_type_markers.get(station_type, 'circle'),
                  size=12,  
                  fill_alpha=0.1,  
                  line_alpha=0.5,
                  legend_label=f'{station_type}')

# Define size categories and colors for centroids based on total count
def get_centroid_size(station_type):
    if station_type not in station_type_counts:
        return 40  # Default size if the station type is not in the counts
    count = station_type_counts[station_type]
    proportion = count / total_count
    
    if proportion <= 0.05:
        return 40  # Small
    elif proportion <= 0.1:
        return 40  # Medium
    elif proportion <= 0.2:
        return 50  # Large
    else:
        return 60  # Extra large

# Update colors and transparency for centroids
centroid_colors = {
    'Tide Station': 'lightyellow',       # Light yellow for Tide Station
    'Groundwater': 'darkgreen',          # Dark green for Groundwater
    'Surface Water': 'blue',             # Blue for Surface Water
    'Water Quality': 'red'               # Red for Water Quality
}

centroid_markers = {
    'Tide Station': 'square',            # Light yellow square for Tide Station
    'Groundwater': 'square',             # Dark green square for Groundwater
    'Surface Water': 'circle',           # Blue circle for Surface Water
    'Water Quality': 'triangle'          # Red triangle for Water Quality
}

# Plot the centroids with larger markers and adjusted transparency
for station_type in centroid_markers.keys():
    if station_type == 'Not known' or station_type not in centroids_merged_df['station_type'].unique():
        continue
    
    # Filter centroids by station_type
    centroid_df = centroids_merged_df[centroids_merged_df['station_type'] == station_type]
    
    # Define size and transparency for centroids
    centroid_color = centroid_colors.get(station_type, 'rgba(255,0,0,0.3)')
    centroid_marker = centroid_markers.get(station_type, 'circle')
    centroid_size = get_centroid_size(station_type)
    fill_alpha = 0.1  # Default transparency
    line_alpha = 5
    
    p.scatter('longitude', 'latitude', source=ColumnDataSource(centroid_df),
              color=centroid_color,
              marker=centroid_marker,
              size=centroid_size,  # Larger size for centroids
              fill_alpha=fill_alpha,  # Adjusted transparency
              line_alpha=line_alpha, 
              legend_label=f'Centroid {station_type}')

# Add hover tool
hover = HoverTool()
hover.tooltips = [("Station Number", "@station_number"),
                   ("County", "@County"),
                   ("Type", "@station_type"),
                   ("Cluster", "@cluster")]
p.add_tools(hover)

# Update legend
p.legend.title = 'Station Type / Centroid'
p.legend.label_text_font_size = '12pt'
p.legend.background_fill_color = '#001f3f'  # Dark blue background for legend
p.legend.border_line_color = 'white'
p.legend.label_text_color = 'white'

# Update axis labels and colors
p.xaxis.axis_label_text_color = 'white'
p.yaxis.axis_label_text_color = 'white'
p.xaxis.major_label_text_color = 'white'
p.yaxis.major_label_text_color = 'white'

# Show the plot
show(p)

# Calculate and display the breakdown of station types
station_type_counts = combined_merged_df['station_type'].value_counts()
total_count = station_type_counts.sum()

# Create a DataFrame for display
station_type_breakdown = pd.DataFrame({
    'Station Type': station_type_counts.index,
    'Count': station_type_counts.values,
    'Percentage': (station_type_counts.values / total_count * 100).round(1)
})

# Define colors for each station type
colors = {
    'Surface Water': 'blue',
    'Groundwater': 'darkgreen',
    'Water Quality': 'red',
    'Not known': 'grey',
    'Unknown': 'grey',
    'Tide Station': 'lightyellow'
}

# Print the breakdown with color
for _, row in station_type_breakdown.iterrows():
    color = colors.get(row['Station Type'], 'black')
    print(f"Station Type: {row['Station Type']}, Count: {row['Count']}, Percentage: {row['Percentage']}%, Color: {color}")


Loading BokehJS ...

c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=1.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=2.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=3.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is k

Station Type: Groundwater, Count: 614, Percentage: 53.6%, Color: darkgreen
Station Type: Surface Water, Count: 276, Percentage: 24.1%, Color: blue
Station Type: Water Quality, Count: 195, Percentage: 17.0%, Color: red
Station Type: Tide Station, Count: 60, Percentage: 5.2%, Color: lightyellow


In [30]:
import pandas as pd
from bokeh.plotting import figure, show
from bokeh.io import output_notebook
from bokeh.models import ColumnDataSource, HoverTool
from sklearn.cluster import KMeans

# Output to notebook
output_notebook()

# Load the CSV files into DataFrames
stations_df = pd.read_csv(r'C:\Users\npwol\Downloads\ca_counties\ContinuousMonitoringStation_20240815171202.csv')
cities_df = pd.read_csv(r'C:\Users\npwol\Downloads\ca_counties\California_cities.csv')

# Rename columns in cities_df to match the columns in stations_df
cities_df = cities_df.rename(columns={
    'latd': 'latitude',
    'longd': 'longitude'
})

# Merge the DataFrames on latitude and longitude
merged_df = pd.merge(stations_df, cities_df[['city', 'population_total', 'area_total_sq_mi', 'latitude', 'longitude']],
                     on=['latitude', 'longitude'],
                     how='left')

# Filter out 'Not known' and 'Unknown' station types
n_clusters_dict = {
    'Tide Station': 1,
    'Surface Water': 7,
    'Groundwater': 4,
    'Water Quality': 4
}

filtered_merged_df = merged_df[merged_df['station_type'].isin(n_clusters_dict.keys())]

# Calculate the total count of each station type and the overall total
station_type_counts = filtered_merged_df['station_type'].value_counts()
total_count = len(filtered_merged_df)

# Initialize lists to hold the centroid data
centroids = []
cluster_labels = []

# Perform K-means clustering for each station_type bin
for station_type, n_clusters in n_clusters_dict.items():
    # Filter data for the current station_type
    type_merged_df = filtered_merged_df[filtered_merged_df['station_type'] == station_type].copy()
    
    # Prepare data for K-means clustering
    coordinates = type_merged_df[['longitude', 'latitude']].values
    
    # Perform K-means clustering with the specified number of clusters
    kmeans = KMeans(n_clusters=n_clusters, random_state=0).fit(coordinates)
    
    # Add cluster labels to the DataFrame
    type_merged_df['cluster'] = kmeans.labels_.astype(str)
    
    # Extract centroids and add to the list
    centroids.append(pd.DataFrame(kmeans.cluster_centers_, columns=['longitude', 'latitude'])
                     .assign(station_type=station_type, cluster=[str(i) for i in range(n_clusters)]))
    
    # Append the data with clusters to the list
    cluster_labels.append(type_merged_df)

# Combine all clustered data and centroids
combined_merged_df = pd.concat(cluster_labels, ignore_index=True)
centroids_merged_df = pd.concat(centroids, ignore_index=True)

# Define colors and markers for station types
station_type_colors = {
    'Surface Water': 'blue',        # Blue for Surface Water
    'Groundwater': 'darkgreen',     # Dark green for Groundwater
    'Water Quality': 'red',         # Red for Water Quality
    'Not known': 'grey',            # Grey for Not Known
    'Unknown': 'grey',              # Grey for Unknown
    'Tide Station': 'lightyellow'   # Yellow for Tide Station
}

station_type_markers = {
    'Surface Water': 'circle',    # Blue circle
    'Groundwater': 'square',      # Dark green square
    'Water Quality': 'triangle',  # Red triangle
    'Not known': '+',             # Grey plus sign
    'Unknown': '+',               # Grey plus sign
    'Tide Station': 'square'      # Yellow square
}

# Define colors and markers for centroids
centroid_colors = {
    'Tide Station': 'lightyellow',       # Light yellow for Tide Station
    'Groundwater': 'darkgreen',          # Dark green for Groundwater
    'Surface Water': 'blue',             # Blue for Surface Water
    'Water Quality': 'red'               # Red for Water Quality
}

centroid_markers = {
    'Tide Station': 'square',            # Light yellow square for Tide Station
    'Groundwater': 'square',             # Dark green square for Groundwater
    'Surface Water': 'circle',           # Blue circle for Surface Water
    'Water Quality': 'triangle'          # Red triangle for Water Quality
}

# Define function to scale marker size based on population
def scale_marker_size(population):
    return min(max(population / 100000, 8), 40)  # Scale size for visibility

# Create ColumnDataSources for plotting
source_combined = ColumnDataSource(combined_merged_df)
source_centroids = ColumnDataSource(centroids_merged_df)

# Create a Bokeh plot
p = figure(width=1000, height=800, title="K-means Clustering by Station Type",
           x_axis_label='Longitude', y_axis_label='Latitude',
           x_range=(-125, -116), y_range=(32, 43),
           background_fill_color='#001f3f',  # Very dark blue background
           border_fill_color='#001f3f',
           outline_line_color='white')

# Plot all stations based on their type
for station_type, marker in station_type_markers.items():
    type_merged_df = combined_merged_df[combined_merged_df['station_type'] == station_type]
    p.scatter(x='longitude', y='latitude', source=ColumnDataSource(type_merged_df),
              color=station_type_colors.get(station_type, 'rgba(128,128,128,0.3)'),
              marker=station_type_markers.get(station_type, 'circle'),
              size=12,  
              fill_alpha=0.1,  
              line_alpha=0.5,
              legend_label=f'{station_type}')

# Plot the centroids with larger markers and adjusted transparency
for station_type in centroid_markers.keys():
    # Filter centroids by station_type
    centroid_merged_df = centroids_merged_df[centroids_merged_df['station_type'] == station_type]
    
    # Define size and transparency for centroids
    centroid_color = centroid_colors.get(station_type, 'rgba(255,0,0,0.3)')
    centroid_marker = centroid_markers.get(station_type, 'circle')
    centroid_size = get_centroid_size(station_type)
    fill_alpha = 0.1  # Semi-transparent fill
    line_alpha = 0.8
    
    p.scatter(x='longitude', y='latitude', source=ColumnDataSource(centroid_merged_df),
              color=centroid_color,
              marker=centroid_marker,
              size=centroid_size,  # Larger size for centroids
              fill_alpha=fill_alpha,  # Adjusted transparency
              line_alpha=line_alpha, 
              legend_label=f'Centroid {station_type}')

# Plot top 10 cities
top_cities = cities_df.sort_values(by='population_total', ascending=False).head(7)
top_cities['size'] = top_cities['population_total'].apply(scale_marker_size)
source_top_cities = ColumnDataSource(top_cities)

p.scatter(x='longitude', y='latitude', source=source_top_cities,
          color='white',  # Use white color for cities
          marker='star',  # Star marker for cities
          size=20,  # Size is based on population
          fill_alpha=0.7,
          legend_label='Top 10 Cities')

# Add HoverTool
hover = HoverTool()
hover.tooltips = [("Station Number", "@station_number"),
                   ("County", "@County"),
                   ("Type", "@station_type"),
                   ("Cluster", "@cluster"),
                   ("City", "@city"),
                   ("Population", "@population_total")]
p.add_tools(hover)

# Update plot appearance
p.legend.title = 'Station Type / City'
p.legend.label_text_font_size = '12pt'
p.legend.background_fill_color = '#001f3f'  # Dark blue background for legend
p.legend.border_line_color = 'white'
p.legend.label_text_color = 'white'

p.xaxis.axis_label_text_color = 'white'
p.yaxis.axis_label_text_color = 'white'
p.xaxis.major_label_text_color = 'white'
p.yaxis.major_label_text_color = 'white'

# Show the plot
show(p)


Loading BokehJS ...

c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=1.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=2.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=3.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is k

In [32]:
import json

# Load GeoJSON data
with open(r'C:\Users\npwol\Downloads\ca_counties\ca_counties.geojson', 'r') as file:
    geojson_data = json.load(file)


In [33]:
from bokeh.models import GeoJSONDataSource

# Create a GeoJSONDataSource object
geo_source = GeoJSONDataSource(geojson=json.dumps(geojson_data))


In [34]:
from bokeh.palettes import Viridis256

# Add polygons to the plot
p.patches(
    'xs', 'ys',  # Use 'xs' and 'ys' for the longitude and latitude arrays
    source=geo_source,
    fill_color='lightgrey',  # Color of the polygons
    line_color='black',  # Color of the polygon borders
    line_width=0.5,  # Width of the polygon borders
    fill_alpha=0.5  # Transparency of the polygons
)


GlyphRenderer(id='p2693', ...)

In [38]:
import pandas as pd
from bokeh.plotting import figure, show
from bokeh.io import output_notebook
from bokeh.models import ColumnDataSource, HoverTool, GeoJSONDataSource
from sklearn.cluster import KMeans
import json

# Output to notebook
output_notebook()

# Load the CSV files into DataFrames
stations_df = pd.read_csv(r'C:\Users\npwol\Downloads\ca_counties\ContinuousMonitoringStation_20240815171202.csv')
cities_df = pd.read_csv(r'C:\Users\npwol\Downloads\ca_counties\California_cities.csv')

# Rename columns in cities_df to match the columns in stations_df
cities_df = cities_df.rename(columns={
    'latd': 'latitude',
    'longd': 'longitude'
})

# Merge the DataFrames on latitude and longitude
merged_df = pd.merge(stations_df, cities_df[['city', 'population_total', 'area_total_sq_mi', 'latitude', 'longitude']],
                     on=['latitude', 'longitude'],
                     how='left')

# Filter out 'Not known' and 'Unknown' station types
n_clusters_dict = {
    'Tide Station': 1,
    'Surface Water': 7,
    'Groundwater': 4,
    'Water Quality': 4
}

filtered_merged_df = merged_df[merged_df['station_type'].isin(n_clusters_dict.keys())]

# Calculate the total count of each station type and the overall total
station_type_counts = filtered_merged_df['station_type'].value_counts()
total_count = len(filtered_merged_df)

# Initialize lists to hold the centroid data
centroids = []
cluster_labels = []

# Perform K-means clustering for each station_type bin
for station_type, n_clusters in n_clusters_dict.items():
    # Filter data for the current station_type
    type_merged_df = filtered_merged_df[filtered_merged_df['station_type'] == station_type].copy()
    
    # Prepare data for K-means clustering
    coordinates = type_merged_df[['longitude', 'latitude']].values
    
    # Perform K-means clustering with the specified number of clusters
    kmeans = KMeans(n_clusters=n_clusters, random_state=0).fit(coordinates)
    
    # Add cluster labels to the DataFrame
    type_merged_df['cluster'] = kmeans.labels_.astype(str)
    
    # Extract centroids and add to the list
    centroids.append(pd.DataFrame(kmeans.cluster_centers_, columns=['longitude', 'latitude'])
                     .assign(station_type=station_type, cluster=[str(i) for i in range(n_clusters)]))
    
    # Append the data with clusters to the list
    cluster_labels.append(type_merged_df)

# Combine all clustered data and centroids
combined_merged_df = pd.concat(cluster_labels, ignore_index=True)
centroids_merged_df = pd.concat(centroids, ignore_index=True)

# Define colors and markers for station types
station_type_colors = {
    'Surface Water': 'blue',
    'Groundwater': 'darkgreen',
    'Water Quality': 'red',
    'Not known': 'grey',
    'Unknown': 'grey',
    'Tide Station': 'lightyellow'
}

station_type_markers = {
    'Surface Water': 'circle',
    'Groundwater': 'square',
    'Water Quality': 'triangle',
    'Not known': '+',
    'Unknown': '+',
    'Tide Station': 'square'
}

# Define colors and markers for centroids
centroid_colors = {
    'Tide Station': 'lightyellow',
    'Groundwater': 'darkgreen',
    'Surface Water': 'blue',
    'Water Quality': 'red'
}

centroid_markers = {
    'Tide Station': 'square',
    'Groundwater': 'square',
    'Surface Water': 'circle',
    'Water Quality': 'triangle'
}

# Define function to scale marker size based on population
def scale_marker_size(population):
    return min(max(population / 100000, 8), 40)

# Create ColumnDataSources for plotting
source_combined = ColumnDataSource(combined_merged_df)
source_centroids = ColumnDataSource(centroids_merged_df)

# Create a Bokeh plot
p = figure(width=1000, height=800, title="K-means Clustering by Station Type",
           x_axis_label='Longitude', y_axis_label='Latitude',
           x_range=(-125, -116.5), y_range=(32, 42.5),
           background_fill_color='#001f3f',
           border_fill_color='#001f3f',
           outline_line_color='white')

# Plot all stations based on their type
for station_type, marker in station_type_markers.items():
    type_merged_df = combined_merged_df[combined_merged_df['station_type'] == station_type]
    p.scatter(x='longitude', y='latitude', source=ColumnDataSource(type_merged_df),
              color=station_type_colors.get(station_type, 'rgba(128,128,128,0.3)'),
              marker=station_type_markers.get(station_type, 'circle'),
              size=12,
              fill_alpha=0.1,
              line_alpha=0.5,
              legend_label=f'{station_type}')

# Plot the centroids with larger markers and adjusted transparency
for station_type in centroid_markers.keys():
    centroid_merged_df = centroids_merged_df[centroids_merged_df['station_type'] == station_type]
    centroid_color = centroid_colors.get(station_type, 'rgba(255,0,0,0.3)')
    centroid_marker = centroid_markers.get(station_type, 'circle')
    centroid_size = 20  # Larger size for centroids
    fill_alpha = 0.1
    line_alpha = 0.8
    
    p.scatter(x='longitude', y='latitude', source=ColumnDataSource(centroid_merged_df),
              color=centroid_color,
              marker=centroid_marker,
              size=centroid_size,
              fill_alpha=fill_alpha,
              line_alpha=line_alpha,
              legend_label=f'Centroid {station_type}')

# Plot top 10 cities
top_cities = cities_df.sort_values(by='population_total', ascending=False).head(7)
top_cities['size'] = top_cities['population_total'].apply(scale_marker_size)
source_top_cities = ColumnDataSource(top_cities)

p.scatter(x='longitude', y='latitude', source=source_top_cities,
          color='white',
          marker='star',
          size=20,
          fill_alpha=0.7,
          legend_label='Top 10 Cities')

# Add HoverTool
hover = HoverTool()
hover.tooltips = [("Station Number", "@station_number"),
                   ("County", "@County"),
                   ("Type", "@station_type"),
                   ("Cluster", "@cluster"),
                   ("City", "@city"),
                   ("Population", "@population_total")]
p.add_tools(hover)

# Load GeoJSON data
with open(r'C:\Users\npwol\Downloads\ca_counties\ca_counties.geojson', 'r') as file:
    geojson_data = json.load(file)

# Create a GeoJSONDataSource object
geo_source = GeoJSONDataSource(geojson=json.dumps(geojson_data))

# Add polygons to the plot
p.patches(
    'xs', 'ys',
    source=geo_source,
    fill_color='lightgrey',
    line_color='black',
    line_width=0.5,
    fill_alpha=0.1
)

# Update plot appearance
p.legend.title = 'Station Type / City'
p.legend.label_text_font_size = '12pt'
p.legend.background_fill_color = '#001f3f'  # Dark blue background for legend
p.legend.border_line_color = 'white'
p.legend.label_text_color = 'white'

p.xaxis.axis_label_text_color = 'white'
p.yaxis.axis_label_text_color = 'white'
p.xaxis.major_label_text_color = 'white'
p.yaxis.major_label_text_color = 'white'

# Show the plot
show(p)


Loading BokehJS ...

c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=1.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=2.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=3.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is k

In [42]:
import pandas as pd
from bokeh.plotting import figure, show
from bokeh.io import output_notebook
from bokeh.models import ColumnDataSource, HoverTool, GeoJSONDataSource
from sklearn.cluster import KMeans
import json

# Output to notebook
output_notebook()

# Load the CSV files into DataFrames
stations_df = pd.read_csv(r'C:\Users\npwol\Downloads\ca_counties\ContinuousMonitoringStation_20240815171202.csv')
cities_df = pd.read_csv(r'C:\Users\npwol\Downloads\ca_counties\California_cities.csv')

# Rename columns in cities_df to match the columns in stations_df
cities_df = cities_df.rename(columns={
    'latd': 'latitude',
    'longd': 'longitude'
})

# Merge the DataFrames on latitude and longitude
merged_df = pd.merge(stations_df, cities_df[['city', 'population_total', 'area_total_sq_mi', 'latitude', 'longitude']],
                     on=['latitude', 'longitude'],
                     how='left')

# Filter out 'Not known' and 'Unknown' station types
n_clusters_dict = {
    'Tide Station': 1,
    'Surface Water': 7,
    'Groundwater': 4,
    'Water Quality': 4
}

filtered_merged_df = merged_df[merged_df['station_type'].isin(n_clusters_dict.keys())]

# Initialize lists to hold the centroid data
centroids = []
cluster_labels = []

# Perform K-means clustering for each station_type bin
for station_type, n_clusters in n_clusters_dict.items():
    # Filter data for the current station_type
    type_merged_df = filtered_merged_df[filtered_merged_df['station_type'] == station_type].copy()
    
    # Prepare data for K-means clustering
    coordinates = type_merged_df[['longitude', 'latitude']].values
    
    # Perform K-means clustering with the specified number of clusters
    kmeans = KMeans(n_clusters=n_clusters, random_state=0).fit(coordinates)
    
    # Add cluster labels to the DataFrame
    type_merged_df['cluster'] = kmeans.labels_.astype(str)
    
    # Extract centroids and add to the list
    centroids.append(pd.DataFrame(kmeans.cluster_centers_, columns=['longitude', 'latitude'])
                     .assign(station_type=station_type, cluster=[str(i) for i in range(n_clusters)]))
    
    # Append the data with clusters to the list
    cluster_labels.append(type_merged_df)

# Combine all clustered data and centroids
combined_merged_df = pd.concat(cluster_labels, ignore_index=True)
centroids_merged_df = pd.concat(centroids, ignore_index=True)

# Define colors and markers for station types
station_type_colors = {
    'Surface Water': 'blue',
    'Groundwater': 'darkgreen',
    'Water Quality': 'red',
    'Not known': 'grey',
    'Unknown': 'grey',
    'Tide Station': 'lightyellow'
}

station_type_markers = {
    'Surface Water': 'circle',
    'Groundwater': 'square',
    'Water Quality': 'triangle',
    'Not known': '+',
    'Unknown': '+',
    'Tide Station': 'square'
}

# Define colors and markers for centroids
centroid_colors = {
    'Tide Station': 'lightyellow',
    'Groundwater': 'darkgreen',
    'Surface Water': 'blue',
    'Water Quality': 'red'
}

centroid_markers = {
    'Tide Station': 'square',
    'Groundwater': 'square',
    'Surface Water': 'circle',
    'Water Quality': 'triangle'
}

# Define function to scale marker size based on population
def scale_marker_size(population):
    return min(max(population / 100000, 8), 40)

# Define function to get centroid size based on station type
def get_centroid_size(station_type):
    return 50  # Fixed size for simplicity; you can adjust based on type if needed

# Create ColumnDataSources for plotting
source_combined = ColumnDataSource(combined_merged_df)
source_centroids = ColumnDataSource(centroids_merged_df)

# Create a Bokeh plot
p = figure(width=1000, height=800, title="K-means Clustering by Station Type",
           x_axis_label='Longitude', y_axis_label='Latitude',
           x_range=(-125, -116.5), y_range=(32.2, 42.2),
           background_fill_color='#001f3f',
           border_fill_color='#001f3f',
           outline_line_color='white')

# Plot all stations based on their type
for station_type, marker in station_type_markers.items():
    type_merged_df = combined_merged_df[combined_merged_df['station_type'] == station_type]
    p.scatter(x='longitude', y='latitude', source=ColumnDataSource(type_merged_df),
              color=station_type_colors.get(station_type, 'rgba(128,128,128,0.3)'),
              marker=station_type_markers.get(station_type, 'circle'),
              size=12,
              fill_alpha=0.1,
              line_alpha=0.5,
              legend_label=f'{station_type}')

# Plot the centroids with larger markers and adjusted transparency
for station_type in centroid_markers.keys():
    centroid_merged_df = centroids_merged_df[centroids_merged_df['station_type'] == station_type]
    centroid_color = centroid_colors.get(station_type, 'rgba(255,0,0,0.3)')
    centroid_marker = centroid_markers.get(station_type, 'circle')
    centroid_size = get_centroid_size(station_type)
    fill_alpha = 0.1
    line_alpha = 0.8
    
    p.scatter(x='longitude', y='latitude', source=ColumnDataSource(centroid_merged_df),
              color=centroid_color,
              marker=centroid_marker,
              size=centroid_size,
              fill_alpha=fill_alpha,
              line_alpha=line_alpha,
              legend_label=f'Centroid {station_type}')

# Plot top 10 cities
top_cities = cities_df.sort_values(by='population_total', ascending=False).head(7)
top_cities['size'] = top_cities['population_total'].apply(scale_marker_size)
source_top_cities = ColumnDataSource(top_cities)

p.scatter(x='longitude', y='latitude', source=source_top_cities,
          color='white',
          marker='star',
          size=20,
          fill_alpha=0.7,
          legend_label='Top 10 Cities')

# Add HoverTool
hover = HoverTool()
hover.tooltips = [("Station Number", "@station_number"),
                   ("County", "@County"),
                   ("Type", "@station_type"),
                   ("Cluster", "@cluster"),
                   ("City", "@city"),
                   ("Population", "@population_total")]
p.add_tools(hover)

# Load GeoJSON data
with open(r'C:\Users\npwol\Downloads\ca_counties\ca_counties.geojson', 'r') as file:
    geojson_data = json.load(file)

# Create a GeoJSONDataSource object
geo_source = GeoJSONDataSource(geojson=json.dumps(geojson_data))

# Add polygons to the plot
p.patches(
    'xs', 'ys',
    source=geo_source,
    fill_color='lightgrey',
    line_color='black',
    line_width=0.5,
    fill_alpha=0.1
)

# Update plot appearance
p.legend.title = 'Station Type / City'
p.legend.label_text_font_size = '12pt'
p.legend.background_fill_color = '#001f3f'
p.legend.border_line_color = 'white'
p.legend.label_text_color = 'white'

p.xaxis.axis_label_text_color = 'white'
p.yaxis.axis_label_text_color = 'white'
p.xaxis.major_label_text_color = 'white'
p.yaxis.major_label_text_color = 'white'

# Show the plot
show(p)


Loading BokehJS ...

c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=1.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=2.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=3.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is k

In [62]:
import pandas as pd
from bokeh.plotting import figure, show
from bokeh.io import output_notebook
from bokeh.models import ColumnDataSource, HoverTool, GeoJSONDataSource, LabelSet
from sklearn.cluster import KMeans
import json

# Output to notebook
output_notebook()

# Load the CSV files into DataFrames
stations_df = pd.read_csv(r'C:\Users\npwol\Downloads\ca_counties\ContinuousMonitoringStation_20240815171202.csv')
cities_df = pd.read_csv(r'C:\Users\npwol\Downloads\ca_counties\California_cities.csv')

# Rename columns in cities_df to match the columns in stations_df
cities_df = cities_df.rename(columns={
    'latd': 'latitude',
    'longd': 'longitude'
})

# Merge the DataFrames on latitude and longitude
merged_df = pd.merge(stations_df, cities_df[['city', 'population_total', 'area_total_sq_mi', 'latitude', 'longitude']],
                     on=['latitude', 'longitude'],
                     how='left')

# Filter out 'Not known' and 'Unknown' station types
n_clusters_dict = {
    'Tide Station': 1,
    'Surface Water': 7,
    'Groundwater': 4,
    'Water Quality': 4
}

filtered_merged_df = merged_df[merged_df['station_type'].isin(n_clusters_dict.keys())]

# Initialize lists to hold the centroid data
centroids = []
cluster_labels = []

# Perform K-means clustering for each station_type bin
for station_type, n_clusters in n_clusters_dict.items():
    # Filter data for the current station_type
    type_merged_df = filtered_merged_df[filtered_merged_df['station_type'] == station_type].copy()
    
    # Prepare data for K-means clustering
    coordinates = type_merged_df[['longitude', 'latitude']].values
    
    # Perform K-means clustering with the specified number of clusters
    kmeans = KMeans(n_clusters=n_clusters, random_state=0).fit(coordinates)
    
    # Add cluster labels to the DataFrame
    type_merged_df['cluster'] = kmeans.labels_.astype(str)
    
    # Extract centroids and add to the list
    centroids.append(pd.DataFrame(kmeans.cluster_centers_, columns=['longitude', 'latitude'])
                     .assign(station_type=station_type, cluster=[str(i) for i in range(n_clusters)]))
    
    # Append the data with clusters to the list
    cluster_labels.append(type_merged_df)

# Combine all clustered data and centroids
combined_merged_df = pd.concat(cluster_labels, ignore_index=True)
centroids_merged_df = pd.concat(centroids, ignore_index=True)

# Define colors and markers for station types
station_type_colors = {
    'Surface Water': 'blue',
    'Groundwater': 'darkgreen',
    'Water Quality': 'red',
    'Not known': 'grey',
    'Unknown': 'grey',
    'Tide Station': 'lightyellow'
}

station_type_markers = {
    'Surface Water': 'circle',
    'Groundwater': 'square',
    'Water Quality': 'triangle',
    'Not known': '+',
    'Unknown': '+',
    'Tide Station': 'square'
}

# Define colors and markers for centroids
centroid_colors = {
    'Tide Station': 'lightyellow',
    'Groundwater': 'darkgreen',
    'Surface Water': 'blue',
    'Water Quality': 'red'
}

centroid_markers = {
    'Tide Station': 'square',
    'Groundwater': 'square',
    'Surface Water': 'circle',
    'Water Quality': 'triangle'
}

# Define function to scale marker size based on population
def scale_marker_size(population):
    return min(max(population / 100000, 8), 40)

# Define function to get centroid size based on station type
def get_centroid_size(station_type):
    return 50  # Fixed size for simplicity; you can adjust based on type if needed

# Create ColumnDataSources for plotting
source_combined = ColumnDataSource(combined_merged_df)
source_centroids = ColumnDataSource(centroids_merged_df)
source_top_cities = ColumnDataSource(cities_df)

# Create a Bokeh plot
p = figure(width=1000, height=800, title="K-means Clustering by Station Type",
           x_axis_label='Longitude', y_axis_label='Latitude',
           x_range=(-125, -116.5), y_range=(32, 42.5),
           background_fill_color='#001f3f',
           border_fill_color='#001f3f',
           outline_line_color='white')

# Plot all stations based on their type
for station_type, marker in station_type_markers.items():
    type_merged_df = combined_merged_df[combined_merged_df['station_type'] == station_type]
    p.scatter(x='longitude', y='latitude', source=ColumnDataSource(type_merged_df),
              color=station_type_colors.get(station_type, 'rgba(128,128,128,0.3)'),
              marker=station_type_markers.get(station_type, 'circle'),
              size=12,
              fill_alpha=0.1,
              line_alpha=0.5,
              legend_label=f'{station_type}')

# Plot the centroids with larger markers and adjusted transparency
for station_type in centroid_markers.keys():
    centroid_merged_df = centroids_merged_df[centroids_merged_df['station_type'] == station_type]
    centroid_color = centroid_colors.get(station_type, 'rgba(255,0,0,0.3)')
    centroid_marker = centroid_markers.get(station_type, 'circle')
    centroid_size = get_centroid_size(station_type)
    fill_alpha = 0.1
    line_alpha = 0.8
    
    p.scatter(x='longitude', y='latitude', source=ColumnDataSource(centroid_merged_df),
              color=centroid_color,
              marker=centroid_marker,
              size=centroid_size,
              fill_alpha=fill_alpha,
              line_alpha=line_alpha,
              legend_label=f'Centroid {station_type}')

# Plot top cities
top_cities = cities_df.sort_values(by='population_total', ascending=False).head(7)
top_cities['size'] = top_cities['population_total'].apply(scale_marker_size)
source_top_cities = ColumnDataSource(top_cities)

# Add city labels
labels = LabelSet(x='longitude', y='latitude', text='city', level='glyph',
                  source=source_top_cities, 
                  x_offset=9, y_offset=11, text_font_size='11pt', text_color='white')

# Add scatter plot for top cities
p.scatter(x='longitude', y='latitude', source=source_top_cities,
          color='white',
          marker='star',
          size=20,
          fill_alpha=0.7,
          legend_label='Top Cities')

p.add_layout(labels)

# Add HoverTool
hover = HoverTool()
hover.tooltips = [("Station Number", "@station_number"),
                   ("County", "@County"),
                   ("Type", "@station_type"),
                   ("Cluster", "@cluster"),
                   ("City", "@city"),
                   ("Population", "@population_total")]
p.add_tools(hover)

# Load GeoJSON data
with open(r'C:\Users\npwol\Downloads\ca_counties\ca_counties.geojson', 'r') as file:
    geojson_data = json.load(file)

# Create a GeoJSONDataSource object
geo_source = GeoJSONDataSource(geojson=json.dumps(geojson_data))

# Add polygons to the plot
p.patches(
    'xs', 'ys',
    source=geo_source,
    fill_color='lightgrey',
    line_color='black',
    line_width=0.5,
    fill_alpha=0.1
)

# Update plot appearance
p.legend.title = 'Station Type / City'
p.legend.label_text_font_size = '12pt'
p.legend.background_fill_color = '#001f3f'
p.legend.border_line_color = 'white'
p.legend.label_text_color = 'white'

p.xaxis.axis_label_text_color = 'white'
p.yaxis.axis_label_text_color = 'white'
p.xaxis.major_label_text_color = 'white'
p.yaxis.major_label_text_color = 'white'

# Show the plot
show(p)


Loading BokehJS ...

c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=1.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=2.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=3.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is k

In [65]:
import pandas as pd
from bokeh.plotting import figure, show
from bokeh.io import output_notebook
from bokeh.models import ColumnDataSource, HoverTool, GeoJSONDataSource, LabelSet, BoxAnnotation
from sklearn.cluster import KMeans
import json

# Output to notebook
output_notebook()

# Load the CSV files into DataFrames
stations_df = pd.read_csv(r'C:\Users\npwol\Downloads\ca_counties\ContinuousMonitoringStation_20240815171202.csv')
cities_df = pd.read_csv(r'C:\Users\npwol\Downloads\ca_counties\California_cities.csv')

# Rename columns in cities_df to match the columns in stations_df
cities_df = cities_df.rename(columns={
    'latd': 'latitude',
    'longd': 'longitude'
})

# Merge the DataFrames on latitude and longitude
merged_df = pd.merge(stations_df, cities_df[['city', 'population_total', 'area_total_sq_mi', 'latitude', 'longitude']],
                     on=['latitude', 'longitude'],
                     how='left')

# Filter out 'Not known' and 'Unknown' station types
n_clusters_dict = {
    'Tide Station': 1,
    'Surface Water': 7,
    'Groundwater': 4,
    'Water Quality': 4
}

filtered_merged_df = merged_df[merged_df['station_type'].isin(n_clusters_dict.keys())]

# Initialize lists to hold the centroid data
centroids = []
cluster_labels = []

# Perform K-means clustering for each station_type bin
for station_type, n_clusters in n_clusters_dict.items():
    # Filter data for the current station_type
    type_merged_df = filtered_merged_df[filtered_merged_df['station_type'] == station_type].copy()
    
    # Prepare data for K-means clustering
    coordinates = type_merged_df[['longitude', 'latitude']].values
    
    # Perform K-means clustering with the specified number of clusters
    kmeans = KMeans(n_clusters=n_clusters, random_state=0).fit(coordinates)
    
    # Add cluster labels to the DataFrame
    type_merged_df['cluster'] = kmeans.labels_.astype(str)
    
    # Extract centroids and add to the list
    centroids.append(pd.DataFrame(kmeans.cluster_centers_, columns=['longitude', 'latitude'])
                     .assign(station_type=station_type, cluster=[str(i) for i in range(n_clusters)]))
    
    # Append the data with clusters to the list
    cluster_labels.append(type_merged_df)

# Combine all clustered data and centroids
combined_merged_df = pd.concat(cluster_labels, ignore_index=True)
centroids_merged_df = pd.concat(centroids, ignore_index=True)

# Define colors and markers for station types
station_type_colors = {
    'Surface Water': 'blue',
    'Groundwater': 'darkgreen',
    'Water Quality': 'red',
    'Not known': 'grey',
    'Unknown': 'grey',
    'Tide Station': 'lightyellow'
}

station_type_markers = {
    'Surface Water': 'circle',
    'Groundwater': 'square',
    'Water Quality': 'triangle',
    'Not known': '+',
    'Unknown': '+',
    'Tide Station': 'square'
}

# Define colors and markers for centroids
centroid_colors = {
    'Tide Station': 'lightyellow',
    'Groundwater': 'darkgreen',
    'Surface Water': 'blue',
    'Water Quality': 'red'
}

centroid_markers = {
    'Tide Station': 'square',
    'Groundwater': 'square',
    'Surface Water': 'circle',
    'Water Quality': 'triangle'
}

# Define function to scale marker size based on population
def scale_marker_size(population):
    return min(max(population / 100000, 8), 40)

# Define function to get centroid size based on station type
def get_centroid_size(station_type):
    return 50  # Fixed size for simplicity; you can adjust based on type if needed

# Create ColumnDataSources for plotting
source_combined = ColumnDataSource(combined_merged_df)
source_centroids = ColumnDataSource(centroids_merged_df)
source_top_cities = ColumnDataSource(cities_df)

# Create a Bokeh plot
p = figure(width=1000, height=800, title="K-means Clustering by Station Type",
           x_axis_label='Longitude', y_axis_label='Latitude',
           x_range=(-125, -116), y_range=(32, 42.5),
           background_fill_color='#001f3f',
           border_fill_color='#001f3f',
           outline_line_color='white')

# Plot all stations based on their type
for station_type, marker in station_type_markers.items():
    type_merged_df = combined_merged_df[combined_merged_df['station_type'] == station_type]
    p.scatter(x='longitude', y='latitude', source=ColumnDataSource(type_merged_df),
              color=station_type_colors.get(station_type, 'rgba(128,128,128,0.3)'),
              marker=station_type_markers.get(station_type, 'circle'),
              size=12,
              fill_alpha=0.1,
              line_alpha=0.5,
              legend_label=f'{station_type}')

# Plot the centroids with larger markers and adjusted transparency
for station_type in centroid_markers.keys():
    centroid_merged_df = centroids_merged_df[centroids_merged_df['station_type'] == station_type]
    centroid_color = centroid_colors.get(station_type, 'rgba(255,0,0,0.3)')
    centroid_marker = centroid_markers.get(station_type, 'circle')
    centroid_size = get_centroid_size(station_type)
    fill_alpha = 0.1
    line_alpha = 0.8
    
    p.scatter(x='longitude', y='latitude', source=ColumnDataSource(centroid_merged_df),
              color=centroid_color,
              marker=centroid_marker,
              size=centroid_size,
              fill_alpha=fill_alpha,
              line_alpha=line_alpha,
              legend_label=f'Centroid {station_type}')

# Plot top cities
top_cities = cities_df.sort_values(by='population_total', ascending=False).head(7)
top_cities['size'] = top_cities['population_total'].apply(scale_marker_size)
source_top_cities = ColumnDataSource(top_cities)

# Add BoxAnnotations behind the labels
for city in top_cities.itertuples():
    p.add_layout(BoxAnnotation(
        left=city.longitude - 0.5 * x_offset,  # Adjust to cover the label area
        right=city.longitude + 0.5 * x_offset, # Adjust to cover the label area
        bottom=city.latitude - 0.5 * y_offset,  # Adjust to cover the label area
        top=city.latitude + 0.5 * y_offset,    # Adjust to cover the label area
        fill_color='black',
        fill_alpha=0.2,
        line_color=None,
        level='underlay'  # Ensure BoxAnnotation is below labels
    ))

# Add the LabelSet with text
labels = LabelSet(x='longitude', y='latitude', text='city', level='glyph',
                  source=source_top_cities, 
                  x_offset=x_offset, y_offset=y_offset, text_font_size='11pt', text_color='white')

# Add scatter plot for top cities
p.scatter(x='longitude', y='latitude', source=source_top_cities,
          color='white',
          marker='star',
          size=20,
          fill_alpha=0.7,
          legend_label='Top Cities')

# Add the labels to the plot
p.add_layout(labels)

# Add HoverTool
hover = HoverTool()
hover.tooltips = [("Station Number", "@station_number"),
                   ("County", "@County"),
                   ("Type", "@station_type"),
                   ("Cluster", "@cluster"),
                   ("City", "@city"),
                   ("Population", "@population_total")]
p.add_tools(hover)

# Load GeoJSON data
with open(r'C:\Users\npwol\Downloads\ca_counties\ca_counties.geojson', 'r') as file:
    geojson_data = json.load(file)

# Create a GeoJSONDataSource object
geo_source = GeoJSONDataSource(geojson=json.dumps(geojson_data))

# Add polygons to the plot
p.patches(
    'xs', 'ys',
    source=geo_source,
    fill_color='lightgrey',
    line_color='black',
    line_width=0.5,
    fill_alpha=0.1
)

# Update plot appearance
p.legend.title = 'Station Type / City'
p.legend.label_text_font_size = '12pt'
p.legend.background_fill_color = '#001f3f'
p.legend.border_line_color = 'white'
p.legend.label_text_color = 'white'

p.xaxis.axis_label_text_color = 'white'
p.yaxis.axis_label_text_color = 'white'
p.xaxis.major_label_text_color = 'white'
p.yaxis.major_label_text_color = 'white'

# Show the plot
show(p)


Loading BokehJS ...

c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=1.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=2.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=3.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is k

In [84]:
import pandas as pd
from bokeh.plotting import figure, show
from bokeh.io import output_notebook
from bokeh.models import ColumnDataSource, HoverTool, GeoJSONDataSource, LabelSet
from sklearn.cluster import KMeans
import json

# Output to notebook
output_notebook()

# Load the CSV files into DataFrames
stations_df = pd.read_csv(r'C:\Users\npwol\Downloads\ca_counties\ContinuousMonitoringStation_20240815171202.csv')
cities_df = pd.read_csv(r'C:\Users\npwol\Downloads\ca_counties\California_cities.csv')

# Rename columns in cities_df to match the columns in stations_df
cities_df = cities_df.rename(columns={
    'latd': 'latitude',
    'longd': 'longitude'
})

# Merge the DataFrames on latitude and longitude
merged_df = pd.merge(stations_df, cities_df[['city', 'population_total', 'area_total_sq_mi', 'latitude', 'longitude']],
                     on=['latitude', 'longitude'],
                     how='left')

# Filter out 'Not known' and 'Unknown' station types
n_clusters_dict = {
    'Tide Station': 1,
    'Surface Water': 7,
    'Groundwater': 4,
    'Water Quality': 4
}

filtered_merged_df = merged_df[merged_df['station_type'].isin(n_clusters_dict.keys())]

# Initialize lists to hold the centroid data
centroids = []
cluster_labels = []

# Perform K-means clustering for each station_type bin
for station_type, n_clusters in n_clusters_dict.items():
    # Filter data for the current station_type
    type_merged_df = filtered_merged_df[filtered_merged_df['station_type'] == station_type].copy()
    
    # Prepare data for K-means clustering
    coordinates = type_merged_df[['longitude', 'latitude']].values
    
    # Perform K-means clustering with the specified number of clusters
    kmeans = KMeans(n_clusters=n_clusters, random_state=0).fit(coordinates)
    
    # Add cluster labels to the DataFrame
    type_merged_df['cluster'] = kmeans.labels_.astype(str)
    
    # Extract centroids and add to the list
    centroids.append(pd.DataFrame(kmeans.cluster_centers_, columns=['longitude', 'latitude'])
                     .assign(station_type=station_type, cluster=[str(i) for i in range(n_clusters)]))
    
    # Append the data with clusters to the list
    cluster_labels.append(type_merged_df)

# Combine all clustered data and centroids
combined_merged_df = pd.concat(cluster_labels, ignore_index=True)
centroids_merged_df = pd.concat(centroids, ignore_index=True)

# Define colors and markers for station types
station_type_colors = {
    'Surface Water': 'blue',
    'Groundwater': 'darkgreen',
    'Water Quality': 'red',
    'Not known': 'grey',
    'Unknown': 'grey',
    'Tide Station': 'orange'
}

station_type_markers = {
    'Surface Water': 'circle',
    'Groundwater': 'square',
    'Water Quality': 'triangle',
    'Not known': '+',
    'Unknown': '+',
    'Tide Station': 'square'
}

# Define colors and markers for centroids
centroid_colors = {
    'Tide Station': 'orange',
    'Groundwater': 'darkgreen',
    'Surface Water': 'blue',
    'Water Quality': 'red'
}

centroid_markers = {
    'Tide Station': 'square',
    'Groundwater': 'square',
    'Surface Water': 'circle',
    'Water Quality': 'triangle'
}

# Define function to scale marker size based on population
def scale_marker_size(population):
    return min(max(population / 100000, 8), 40)

# Define function to get centroid size based on station type
def get_centroid_size(station_type):
    return 60  # Fixed size for simplicity; you can adjust based on type if needed

# Create ColumnDataSources for plotting
source_combined = ColumnDataSource(combined_merged_df)
source_centroids = ColumnDataSource(centroids_merged_df)
source_top_cities = ColumnDataSource(cities_df)

# Create a Bokeh plot
p = figure(width=1000, height=800, title="K-means Clustering by Station Type",
           x_axis_label='Longitude', y_axis_label='Latitude',
           x_range=(-124.5, -116), y_range=(32, 42.5),
           background_fill_color='#000022',  # Darker blue background
           border_fill_color='#000022',
           outline_line_color='white')

# Plot all stations based on their type
for station_type, marker in station_type_markers.items():
    type_merged_df = combined_merged_df[combined_merged_df['station_type'] == station_type]
    p.scatter(x='longitude', y='latitude', source=ColumnDataSource(type_merged_df),
              color=station_type_colors.get(station_type, 'rgba(128,128,128,0.3)'),
              marker=station_type_markers.get(station_type, 'circle'),
              size=12,
              fill_alpha=0.1,
              line_alpha=0.5,
              legend_label=f'{station_type}')

# Plot the centroids with larger markers and adjusted transparency
for station_type in centroid_markers.keys():
    centroid_merged_df = centroids_merged_df[centroids_merged_df['station_type'] == station_type]
    centroid_color = centroid_colors.get(station_type, 'rgba(255,0,0,0.3)')
    centroid_marker = centroid_markers.get(station_type, 'circle')
    centroid_size = get_centroid_size(station_type)
    fill_alpha = 0.1
    line_alpha = 0.8
    
    p.scatter(x='longitude', y='latitude', source=ColumnDataSource(centroid_merged_df),
              color=centroid_color,
              marker=centroid_marker,
              size=centroid_size,
              fill_alpha=fill_alpha,
              line_alpha=line_alpha,
              legend_label=f'Centroid {station_type}')

# Plot top cities
top_cities = cities_df.sort_values(by='population_total', ascending=False).head(7)
top_cities['size'] = top_cities['population_total'].apply(scale_marker_size)
source_top_cities = ColumnDataSource(top_cities)

# Add the LabelSet with text
x_offset = 10
y_offset = 10
labels = LabelSet(x='longitude', y='latitude', text='city', level='glyph',
                  source=source_top_cities, 
                  x_offset=x_offset, y_offset=y_offset, text_font_size='15pt', text_color='lightyellow', text_alpha=1)

# Add scatter plot for top cities
p.scatter(x='longitude', y='latitude', source=source_top_cities,
          color='lightyellow',
          marker='star',
          size=20,
          fill_alpha=1,
          legend_label='Top Cities')

# Add the labels to the plot
p.add_layout(labels)

# Add HoverTool
hover = HoverTool()
hover.tooltips = [("Station Number", "@station_number"),
                   ("County", "@County"),
                   ("Type", "@station_type"),
                   ("Cluster", "@cluster"),
                   ("City", "@city"),
                   ("Population", "@population_total")]
p.add_tools(hover)

# Load GeoJSON data
with open(r'C:\Users\npwol\Downloads\ca_counties\ca_counties.geojson', 'r') as file:
    geojson_data = json.load(file)

# Create a GeoJSONDataSource object
geo_source = GeoJSONDataSource(geojson=json.dumps(geojson_data))

# Add polygons to the plot
p.patches(
    'xs', 'ys',
    source=geo_source,
    fill_color='lightgrey',
    line_color='black',
    line_width=0.5,
    fill_alpha=0.1
)

# Update plot appearance
p.legend.title = 'Station Type / City'
p.legend.label_text_font_size = '12pt'
p.legend.background_fill_color = '#000022'  # Darker blue background for legend
p.legend.border_line_color = 'white'
p.legend.label_text_color = 'white'

p.xaxis.axis_label_text_color = 'white'
p.yaxis.axis_label_text_color = 'white'
p.xaxis.major_label_text_color = 'white'
p.yaxis.major_label_text_color = 'white'

# Show the plot
show(p)


Loading BokehJS ...

c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=1.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=2.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=3.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is k

In [87]:
import pandas as pd
from bokeh.plotting import figure, show
from bokeh.io import output_notebook
from bokeh.models import ColumnDataSource, HoverTool, GeoJSONDataSource, LabelSet
from sklearn.cluster import KMeans
import json

# Output to notebook
output_notebook()

# Load the CSV files into DataFrames
stations_df = pd.read_csv(r'C:\Users\npwol\Downloads\ca_counties\ContinuousMonitoringStation_20240815171202.csv')
cities_df = pd.read_csv(r'C:\Users\npwol\Downloads\ca_counties\California_cities.csv')

# Rename columns in cities_df to match the columns in stations_df
cities_df = cities_df.rename(columns={
    'latd': 'latitude',
    'longd': 'longitude'
})

# Merge the DataFrames on latitude and longitude
merged_df = pd.merge(stations_df, cities_df[['city', 'population_total', 'area_total_sq_mi', 'latitude', 'longitude']],
                     on=['latitude', 'longitude'],
                     how='left')

# Filter out 'Not known' and 'Unknown' station types
n_clusters_dict = {
    'Tide Station': 1,
    'Surface Water': 7,
    'Groundwater': 4,
    'Water Quality': 4
}

filtered_merged_df = merged_df[merged_df['station_type'].isin(n_clusters_dict.keys())]

# Initialize lists to hold the centroid data
centroids = []
cluster_labels = []

# Perform K-means clustering for each station_type bin
for station_type, n_clusters in n_clusters_dict.items():
    # Filter data for the current station_type
    type_merged_df = filtered_merged_df[filtered_merged_df['station_type'] == station_type].copy()
    
    # Prepare data for K-means clustering
    coordinates = type_merged_df[['longitude', 'latitude']].values
    
    # Perform K-means clustering with the specified number of clusters
    kmeans = KMeans(n_clusters=n_clusters, random_state=0).fit(coordinates)
    
    # Add cluster labels to the DataFrame
    type_merged_df['cluster'] = kmeans.labels_.astype(str)
    
    # Extract centroids and add to the list
    centroids.append(pd.DataFrame(kmeans.cluster_centers_, columns=['longitude', 'latitude'])
                     .assign(station_type=station_type, cluster=[str(i) for i in range(n_clusters)]))
    
    # Append the data with clusters to the list
    cluster_labels.append(type_merged_df)

# Combine all clustered data and centroids
combined_merged_df = pd.concat(cluster_labels, ignore_index=True)
centroids_merged_df = pd.concat(centroids, ignore_index=True)

# Define colors and markers for station types
station_type_colors = {
    'Surface Water': 'blue',
    'Groundwater': 'darkgreen',
    'Water Quality': 'red',
    'Not known': 'grey',
    'Unknown': 'grey',
    'Tide Station': 'orange'
}

station_type_markers = {
    'Surface Water': 'circle',
    'Groundwater': 'square',
    'Water Quality': 'triangle',
    'Not known': '+',
    'Unknown': '+',
    'Tide Station': 'square'
}

# Define colors and markers for centroids
centroid_colors = {
    'Tide Station': 'orange',
    'Groundwater': 'darkgreen',
    'Surface Water': 'blue',
    'Water Quality': 'red'
}

centroid_markers = {
    'Tide Station': 'square',
    'Groundwater': 'square',
    'Surface Water': 'circle',
    'Water Quality': 'triangle'
}

# Define function to scale marker size based on population
def scale_marker_size(population):
    return min(max(population / 100000, 8), 40)

# Define function to get centroid size based on station type
def get_centroid_size(station_type):
    return 60  # Fixed size for simplicity; you can adjust based on type if needed

# Create ColumnDataSources for plotting
source_combined = ColumnDataSource(combined_merged_df)
source_centroids = ColumnDataSource(centroids_merged_df)
source_top_cities = ColumnDataSource(cities_df)

# Create a Bokeh plot
p = figure(width=1000, height=800, title="K-means Clustering by Station Type",
           x_axis_label='Longitude', y_axis_label='Latitude',
           x_range=(-124.5, -116), y_range=(32, 42.5),
           background_fill_color='#000022',  # Darker blue background
           border_fill_color='#000022',
           outline_line_color='white')

# Plot all stations based on their type
for station_type, marker in station_type_markers.items():
    type_merged_df = combined_merged_df[combined_merged_df['station_type'] == station_type]
    scatter_source = ColumnDataSource(type_merged_df)
    p.scatter(x='longitude', y='latitude', source=scatter_source,
              color=station_type_colors.get(station_type, 'rgba(128,128,128,0.3)'),
              marker=station_type_markers.get(station_type, 'circle'),
              size=12,
              fill_alpha=0.1,
              line_alpha=0.5,
              legend_label=f'{station_type}')
    
    # Add HoverTool for stations only
    hover_tool = HoverTool(renderers=[p.renderers[-1]])  # Apply to the last scatter plot
    hover_tool.tooltips = [("Station Number", "@station_number"),
                           ("County", "@County"),
                           ("Type", "@station_type"),
                           ("Cluster", "@cluster"),
                           ("City", "@city"),
                           ("Population", "@population_total")]
    p.add_tools(hover_tool)

# Plot the centroids with larger markers and adjusted transparency
for station_type in centroid_markers.keys():
    centroid_merged_df = centroids_merged_df[centroids_merged_df['station_type'] == station_type]
    centroid_color = centroid_colors.get(station_type, 'rgba(255,0,0,0.3)')
    centroid_marker = centroid_markers.get(station_type, 'circle')
    centroid_size = get_centroid_size(station_type)
    fill_alpha = 0.1
    line_alpha = 0.8
    
    p.scatter(x='longitude', y='latitude', source=ColumnDataSource(centroid_merged_df),
              color=centroid_color,
              marker=centroid_marker,
              size=centroid_size,
              fill_alpha=fill_alpha,
              line_alpha=line_alpha,
              legend_label=f'Centroid {station_type}')

# Plot top cities
top_cities = cities_df.sort_values(by='population_total', ascending=False).head(7)
top_cities['size'] = top_cities['population_total'].apply(scale_marker_size)
source_top_cities = ColumnDataSource(top_cities)

# Add the LabelSet with text
x_offset = 10
y_offset = 10
labels = LabelSet(x='longitude', y='latitude', text='city', level='glyph',
                  source=source_top_cities, 
                  x_offset=x_offset, y_offset=y_offset, text_font_size='15pt', text_color='lightyellow', text_alpha=1)

# Add scatter plot for top cities
p.scatter(x='longitude', y='latitude', source=source_top_cities,
          color='lightyellow',
          marker='star',
          size=20,
          fill_alpha=1,
          legend_label='Top Cities')

# Add the labels to the plot
p.add_layout(labels)

# Add HoverTool specifically for stations
hover_tool = HoverTool()
hover_tool.tooltips = [("Station Number", "@station_number"),
                       ("County", "@County"),
                       ("Type", "@station_type"),
                       ("Cluster", "@cluster"),
                       ("City", "@city"),
                       ("Population", "@population_total")]
p.add_tools(hover_tool)

# Load GeoJSON data
with open(r'C:\Users\npwol\Downloads\ca_counties\ca_counties.geojson', 'r') as file:
    geojson_data = json.load(file)

# Create a GeoJSONDataSource object
geo_source = GeoJSONDataSource(geojson=json.dumps(geojson_data))

# Add polygons to the plot
p.patches(
    'xs', 'ys',
    source=geo_source,
    fill_color='lightgrey',
    line_color='black',
    line_width=0.5,
    fill_alpha=0.1
)

# Update plot appearance
p.legend.title = 'Station Type / City'
p.legend.label_text_font_size = '12pt'
p.legend.background_fill_color = '#000022'  # Darker blue background for legend
p.legend.border_line_color = 'white'
p.legend.label_text_color = 'white'

p.xaxis.axis_label_text_color = 'white'
p.yaxis.axis_label_text_color = 'white'
p.xaxis.major_label_text_color = 'white'
p.yaxis.major_label_text_color = 'white'

# Show the plot
show(p)


Loading BokehJS ...

c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=1.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=2.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=3.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is k

In [86]:
import pandas as pd
from bokeh.plotting import figure, show
from bokeh.io import output_notebook
from bokeh.models import ColumnDataSource, HoverTool, GeoJSONDataSource, LabelSet
from sklearn.cluster import KMeans
import json

# Output to notebook
output_notebook()

# Load the CSV files into DataFrames
stations_df = pd.read_csv(r'C:\Users\npwol\Downloads\ca_counties\ContinuousMonitoringStation_20240815171202.csv')
cities_df = pd.read_csv(r'C:\Users\npwol\Downloads\ca_counties\California_cities.csv')

# Rename columns in cities_df to match the columns in stations_df
cities_df = cities_df.rename(columns={
    'latd': 'latitude',
    'longd': 'longitude'
})

# Merge the DataFrames on latitude and longitude
merged_df = pd.merge(stations_df, cities_df[['city', 'population_total', 'area_total_sq_mi', 'latitude', 'longitude']],
                     on=['latitude', 'longitude'],
                     how='left')


# Combine all clustered data and centroids
combined_merged_df = pd.concat(cluster_labels, ignore_index=True)


# Define colors and markers for station types
station_type_colors = {
    'Surface Water': 'blue',
    'Groundwater': 'darkgreen',
    'Water Quality': 'red',
    'Not known': 'grey',
    'Unknown': 'grey',
    'Tide Station': 'orange'
}

station_type_markers = {
    'Surface Water': 'circle',
    'Groundwater': 'square',
    'Water Quality': 'triangle',
    'Not known': '+',
    'Unknown': '+',
    'Tide Station': 'square'
}

# Define colors and markers for centroids
centroid_colors = {
    'Tide Station': 'orange',
    'Groundwater': 'darkgreen',
    'Surface Water': 'blue',
    'Water Quality': 'red'
}


# Define function to scale marker size based on population
def scale_marker_size(population):
    return min(max(population / 100000, 8), 40)


# Create ColumnDataSources for plotting
source_combined = ColumnDataSource(combined_merged_df)

source_top_cities = ColumnDataSource(cities_df)

# Create a Bokeh plot
p = figure(width=1000, height=800, title="K-means Clustering by Station Type",
           x_axis_label='Longitude', y_axis_label='Latitude',
           x_range=(-124.5, -116), y_range=(32, 42.5),
           background_fill_color='#000022',  # Darker blue background
           border_fill_color='#000022',
           outline_line_color='white')

# Plot all stations based on their type
for station_type, marker in station_type_markers.items():
    type_merged_df = combined_merged_df[combined_merged_df['station_type'] == station_type]
    p.scatter(x='longitude', y='latitude', source=ColumnDataSource(type_merged_df),
              color=station_type_colors.get(station_type, 'rgba(128,128,128,0.3)'),
              marker=station_type_markers.get(station_type, 'circle'),
              size=12,
              fill_alpha=0.1,
              line_alpha=0.5,
              legend_label=f'{station_type}')


# Plot top cities
top_cities = cities_df.sort_values(by='population_total', ascending=False).head(7)
top_cities['size'] = top_cities['population_total'].apply(scale_marker_size)
source_top_cities = ColumnDataSource(top_cities)

# Add the LabelSet with text
x_offset = 10
y_offset = 10
labels = LabelSet(x='longitude', y='latitude', text='city', level='glyph',
                  source=source_top_cities, 
                  x_offset=x_offset, y_offset=y_offset, text_font_size='15pt', text_color='lightyellow', text_alpha=1)

# Add scatter plot for top cities
p.scatter(x='longitude', y='latitude', source=source_top_cities,
          color='lightyellow',
          marker='star',
          size=20,
          fill_alpha=1,
          legend_label='Top Cities')

# Add the labels to the plot
p.add_layout(labels)

# Add HoverTool
hover = HoverTool()
hover.tooltips = [("Station Number", "@station_number"),
                   ("County", "@County"),
                   ("Type", "@station_type"),
                   ("Cluster", "@cluster"),
                   ("City", "@city"),
                   ("Population", "@population_total")]
p.add_tools(hover)

# Load GeoJSON data
with open(r'C:\Users\npwol\Downloads\ca_counties\ca_counties.geojson', 'r') as file:
    geojson_data = json.load(file)

# Create a GeoJSONDataSource object
geo_source = GeoJSONDataSource(geojson=json.dumps(geojson_data))

# Add polygons to the plot
p.patches(
    'xs', 'ys',
    source=geo_source,
    fill_color='lightgrey',
    line_color='black',
    line_width=0.5,
    fill_alpha=0.1
)

# Update plot appearance
p.legend.title = 'Station Type / City'
p.legend.label_text_font_size = '12pt'
p.legend.background_fill_color = '#000022'  # Darker blue background for legend
p.legend.border_line_color = 'white'
p.legend.label_text_color = 'white'

p.xaxis.axis_label_text_color = 'white'
p.yaxis.axis_label_text_color = 'white'
p.xaxis.major_label_text_color = 'white'
p.yaxis.major_label_text_color = 'white'

# Show the plot
show(p)


Loading BokehJS ...

In [95]:
import pandas as pd
from bokeh.plotting import figure, show
from bokeh.io import output_notebook
from bokeh.models import ColumnDataSource, HoverTool, GeoJSONDataSource, LabelSet
from sklearn.cluster import KMeans
import json

# Output to notebook
output_notebook()

# Load the CSV files into DataFrames
stations_df = pd.read_csv(r'C:\Users\npwol\Downloads\ca_counties\ContinuousMonitoringStation_20240815171202.csv')
cities_df = pd.read_csv(r'C:\Users\npwol\Downloads\ca_counties\California_cities.csv')

# Rename columns in cities_df to match the columns in stations_df
cities_df = cities_df.rename(columns={
    'latd': 'latitude',
    'longd': 'longitude'
})

# Merge the DataFrames on latitude and longitude
merged_df = pd.merge(stations_df, cities_df[['city', 'population_total', 'area_total_sq_mi', 'latitude', 'longitude']],
                     on=['latitude', 'longitude'],
                     how='left')

# Filter out 'Not known' and 'Unknown' station types
n_clusters_dict = {
    'Tide Station': 1,
    'Surface Water': 7,
    'Groundwater': 4,
    'Water Quality': 4
}

filtered_merged_df = merged_df[merged_df['station_type'].isin(n_clusters_dict.keys())]

# Initialize lists to hold the centroid data
centroids = []
cluster_labels = []

# Perform K-means clustering for each station_type bin
for station_type, n_clusters in n_clusters_dict.items():
    # Filter data for the current station_type
    type_merged_df = filtered_merged_df[filtered_merged_df['station_type'] == station_type].copy()
    
    # Prepare data for K-means clustering
    coordinates = type_merged_df[['longitude', 'latitude']].values
    
    # Perform K-means clustering with the specified number of clusters
    kmeans = KMeans(n_clusters=n_clusters, random_state=0).fit(coordinates)
    
    # Add cluster labels to the DataFrame
    type_merged_df['cluster'] = kmeans.labels_.astype(str)
    
    # Extract centroids and add to the list
    centroids.append(pd.DataFrame(kmeans.cluster_centers_, columns=['longitude', 'latitude'])
                     .assign(station_type=station_type, cluster=[str(i) for i in range(n_clusters)]))
    
    # Append the data with clusters to the list
    cluster_labels.append(type_merged_df)

# Combine all clustered data and centroids
combined_merged_df = pd.concat(cluster_labels, ignore_index=True)
centroids_merged_df = pd.concat(centroids, ignore_index=True)

# Define colors and markers for station types
station_type_colors = {
    'Surface Water': 'blue',
    'Groundwater': 'darkgreen',
    'Water Quality': 'red',
    'Not known': 'grey',
    'Unknown': 'grey',
    'Tide Station': 'orange'
}

station_type_markers = {
    'Surface Water': 'circle',
    'Groundwater': 'square',
    'Water Quality': 'triangle',
    'Not known': '+',
    'Unknown': '+',
    'Tide Station': 'square'
}

# Define colors and markers for centroids
centroid_colors = {
    'Surface Water': 'blue',
    'Groundwater': 'darkgreen',
    'Water Quality': 'red',
    'Tide Station': 'orange'
}

centroid_markers = {
    'Surface Water': 'circle',
    'Groundwater': 'square',
    'Water Quality': 'triangle',
    'Tide Station': 'square'
}

# Define function to get centroid size
def get_centroid_size(station_type):
    return 60  

# Create ColumnDataSources for plotting
source_combined = ColumnDataSource(combined_merged_df)
source_centroids = ColumnDataSource(centroids_merged_df)
source_top_cities = ColumnDataSource(cities_df)

# Create a Bokeh plot
p = figure(width=1000, height=800, title="K-means Clustering by Station Type",
           x_axis_label='Longitude', y_axis_label='Latitude',
           x_range=(-124.5, -116), y_range=(32, 42.5),
           background_fill_color='#000022',  
           border_fill_color='#000022',
           outline_line_color='white')

# Plot all stations based on their type
for station_type, marker in station_type_markers.items():
    type_merged_df = combined_merged_df[combined_merged_df['station_type'] == station_type]
    scatter_source = ColumnDataSource(type_merged_df)
    p.scatter(x='longitude', y='latitude', source=scatter_source,
              color=station_type_colors.get(station_type, 'rgba(128,128,128,0.3)'),
              marker=station_type_markers.get(station_type, 'circle'),
              size=12,
              fill_alpha=0.1,
              line_alpha=0.5,
              legend_label=f'{station_type}')
    
    # Add HoverTool for stations only
    hover_tool = HoverTool(renderers=[p.renderers[-1]])  
    hover_tool.tooltips = [("Station Number", "@station_number"),
                           ("County", "@County"),
                           ("Type", "@station_type"),
                           ("Cluster", "@cluster"),
                           ("City", "@city"),
                           ("Population", "@population_total")]
    p.add_tools(hover_tool)

# Plot the centroids with larger markers and adjusted transparency
for station_type in centroid_markers.keys():
    centroid_merged_df = centroids_merged_df[centroids_merged_df['station_type'] == station_type]
    centroid_color = centroid_colors.get(station_type, 'rgba(255,0,0,0.3)')
    fill_alpha = 0.1
    line_alpha = 0.8
    
    p.scatter(x='longitude', y='latitude', source=ColumnDataSource(centroid_merged_df),
              color=centroid_color,
              marker=centroid_marker,
              size=centroid_size,
              fill_alpha=fill_alpha,
              line_alpha=line_alpha,
              legend_label=f'Centroid {station_type}')
    
    # Add HoverTool for centroids only
    hover_tool = HoverTool(renderers=[p.renderers[-1]])  
    hover_tool.tooltips = [("Station Type", "@station_type")]
    p.add_tools(hover_tool)

# Plot top cities
top_cities = cities_df.sort_values(by='population_total', ascending=False).head(7)
top_cities['size'] = top_cities['population_total'].apply(scale_marker_size)
source_top_cities = ColumnDataSource(top_cities)

# Add the LabelSet with text
x_offset = 10
y_offset = 10
labels = LabelSet(x='longitude', y='latitude', text='city', level='glyph',
                  source=source_top_cities, 
                  x_offset=x_offset, y_offset=y_offset, text_font_size='15pt', text_color='lightyellow', text_alpha=1)

# Add scatter plot for top cities
p.scatter(x='longitude', y='latitude', source=source_top_cities,
          color='lightyellow',
          marker='star',
          size=20,
          fill_alpha=1,
          legend_label='Top Cities')

# Add the labels to the plot
p.add_layout(labels)

# Load GeoJSON data
with open(r'C:\Users\npwol\Downloads\ca_counties\ca_counties.geojson', 'r') as file:
    geojson_data = json.load(file)

# Create a GeoJSONDataSource object
geo_source = GeoJSONDataSource(geojson=json.dumps(geojson_data))

# Add polygons to the plot
p.patches(
    'xs', 'ys',
    source=geo_source,
    fill_color='lightgrey',
    line_color='black',
    line_width=0.5,
    fill_alpha=0.1
)

# Update plot appearance
p.legend.title = 'Station Type / City'
p.legend.label_text_font_size = '12pt'
p.legend.background_fill_color = '#000022'  
p.legend.border_line_color = 'white'
p.legend.label_text_color = 'white'

p.xaxis.axis_label_text_color = 'white'
p.yaxis.axis_label_text_color = 'white'
p.xaxis.major_label_text_color = 'white'
p.yaxis.major_label_text_color = 'white'

# Show the plot
show(p)


Loading BokehJS ...

c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=1.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=2.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=3.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is k

In [96]:
import pandas as pd
from bokeh.plotting import figure, show
from bokeh.io import output_notebook
from bokeh.models import ColumnDataSource, HoverTool, GeoJSONDataSource, LabelSet
from sklearn.cluster import KMeans
import json

# Output to notebook
output_notebook()

# Load the CSV files into DataFrames
stations_df = pd.read_csv(r'C:\Users\npwol\Downloads\ca_counties\ContinuousMonitoringStation_20240815171202.csv')
cities_df = pd.read_csv(r'C:\Users\npwol\Downloads\ca_counties\California_cities.csv')

# Rename columns in cities_df to match the columns in stations_df
cities_df = cities_df.rename(columns={
    'latd': 'latitude',
    'longd': 'longitude'
})

# Merge the DataFrames on latitude and longitude
merged_df = pd.merge(stations_df, cities_df[['city', 'population_total', 'area_total_sq_mi', 'latitude', 'longitude']],
                     on=['latitude', 'longitude'],
                     how='left')

# Filter out 'Not known' and 'Unknown' station types
n_clusters_dict = {
    'Tide Station': 1,
    'Surface Water': 7,
    'Groundwater': 4,
    'Water Quality': 4
}

filtered_merged_df = merged_df[merged_df['station_type'].isin(n_clusters_dict.keys())]

# Initialize lists to hold the centroid data
centroids = []
cluster_labels = []

# Perform K-means clustering for each station_type bin
for station_type, n_clusters in n_clusters_dict.items():
    # Filter data for the current station_type
    type_merged_df = filtered_merged_df[filtered_merged_df['station_type'] == station_type].copy()
    
    # Prepare data for K-means clustering
    coordinates = type_merged_df[['longitude', 'latitude']].values
    
    # Perform K-means clustering with the specified number of clusters
    kmeans = KMeans(n_clusters=n_clusters, random_state=0).fit(coordinates)
    
    # Add cluster labels to the DataFrame
    type_merged_df['cluster'] = kmeans.labels_.astype(str)
    
    # Extract centroids and add to the list
    centroids.append(pd.DataFrame(kmeans.cluster_centers_, columns=['longitude', 'latitude'])
                     .assign(station_type=station_type, cluster=[str(i) for i in range(n_clusters)]))
    
    # Append the data with clusters to the list
    cluster_labels.append(type_merged_df)

# Combine all clustered data and centroids
combined_merged_df = pd.concat(cluster_labels, ignore_index=True)
centroids_merged_df = pd.concat(centroids, ignore_index=True)

# Define colors and markers for station types
station_type_colors = {
    'Surface Water': 'blue',
    'Groundwater': 'darkgreen',
    'Water Quality': 'red',
    'Not known': 'grey',
    'Unknown': 'grey',
    'Tide Station': 'orange'
}

station_type_markers = {
    'Surface Water': 'circle',
    'Groundwater': 'square',
    'Water Quality': 'triangle',
    'Not known': '+',
    'Unknown': '+',
    'Tide Station': 'square'
}

# Define colors and markers for centroids
centroid_colors = {
    'Surface Water': 'blue',
    'Groundwater': 'darkgreen',
    'Water Quality': 'red',
    'Tide Station': 'orange'
}

centroid_markers = {
    'Surface Water': 'circle',
    'Groundwater': 'square',
    'Water Quality': 'triangle',
    'Tide Station': 'square'
}

# Define function to get centroid size
def get_centroid_size(station_type):
    return 60  

# Create ColumnDataSources for plotting
source_combined = ColumnDataSource(combined_merged_df)
source_centroids = ColumnDataSource(centroids_merged_df)
source_top_cities = ColumnDataSource(cities_df)

# Create a Bokeh plot
p = figure(width=1000, height=800, title="K-means Clustering by Station Type",
           x_axis_label='Longitude', y_axis_label='Latitude',
           x_range=(-124.5, -116), y_range=(32, 42.5),
           background_fill_color='#000022',  
           border_fill_color='#000022',
           outline_line_color='white')

# Plot the centroids with larger markers and adjusted transparency
for station_type in centroid_markers.keys():
    centroid_merged_df = centroids_merged_df[centroids_merged_df['station_type'] == station_type]
    centroid_color = centroid_colors.get(station_type, 'rgba(255,0,0,0.3)')
    fill_alpha = 0.1
    line_alpha = 0.8
    
    p.scatter(x='longitude', y='latitude', source=ColumnDataSource(centroid_merged_df),
              color=centroid_color,
              marker=centroid_marker,
              size=centroid_size,
              fill_alpha=fill_alpha,
              line_alpha=line_alpha,
              legend_label=f'Centroid {station_type}')
    
    # Add HoverTool for centroids only
    hover_tool = HoverTool(renderers=[p.renderers[-1]])  
    hover_tool.tooltips = [("Station Type", "@station_type")]
    p.add_tools(hover_tool)

# Plot top cities
top_cities = cities_df.sort_values(by='population_total', ascending=False).head(7)
top_cities['size'] = top_cities['population_total'].apply(scale_marker_size)
source_top_cities = ColumnDataSource(top_cities)

# Add the LabelSet with text
x_offset = 10
y_offset = 10
labels = LabelSet(x='longitude', y='latitude', text='city', level='glyph',
                  source=source_top_cities, 
                  x_offset=x_offset, y_offset=y_offset, text_font_size='15pt', text_color='lightyellow', text_alpha=1)

# Add scatter plot for top cities
p.scatter(x='longitude', y='latitude', source=source_top_cities,
          color='lightyellow',
          marker='star',
          size=20,
          fill_alpha=1,
          legend_label='Top Cities')

# Add the labels to the plot
p.add_layout(labels)

# Load GeoJSON data
with open(r'C:\Users\npwol\Downloads\ca_counties\ca_counties.geojson', 'r') as file:
    geojson_data = json.load(file)

# Create a GeoJSONDataSource object
geo_source = GeoJSONDataSource(geojson=json.dumps(geojson_data))

# Add polygons to the plot
p.patches(
    'xs', 'ys',
    source=geo_source,
    fill_color='lightgrey',
    line_color='black',
    line_width=0.5,
    fill_alpha=0.1
)

# Update plot appearance
p.legend.title = 'Station Type / City'
p.legend.label_text_font_size = '12pt'
p.legend.background_fill_color = '#000022'  
p.legend.border_line_color = 'white'
p.legend.label_text_color = 'white'

p.xaxis.axis_label_text_color = 'white'
p.yaxis.axis_label_text_color = 'white'
p.xaxis.major_label_text_color = 'white'
p.yaxis.major_label_text_color = 'white'

# Show the plot
show(p)


Loading BokehJS ...

c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=1.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=2.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=3.
  warnings.warn(
c:\Users\npwol\anaconda3\envs\dev\lib\site-packages\sklearn\cluster\_kmeans.py:1446: UserWarning: KMeans is k